In [ ]:
import os
import sys

import torchvision.transforms as T
from torch.utils.data import DataLoader, random_split

import hydra
import pytorch_lightning as pl
from pytorch_lightning import LightningModule, Trainer
from dotenv import load_dotenv, dotenv_values
from sklearn.datasets import fetch_california_housing

sys.argv = ['']
# 환경변수 읽기
if (python_path := dotenv_values().get('PYTHONPATH')) and python_path not in sys.path: sys.path.append(python_path)

from src.models.RegressionDNN import RegressionDNN
from src.dataset.SimpleRegressionDataset import SimpleRegressionDataset
from sklearn.model_selection import train_test_split
from src.utils import config

# 데이터 준비 함수
def prepare_data(batch_size=64, num_workers=4):
    
    # 1. 데이터 로드
    data = fetch_california_housing()
    X, y = data.data, data.target

    # 2. 데이터 분할
    X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)

    # 3. Dataset 생성
    train_dataset = SimpleRegressionDataset(X_train, y_train)
    test_dataset = SimpleRegressionDataset(X_test, y_test, scaler=train_dataset.scaler)
    
    # DataLoader 생성
    train_loader = DataLoader(train_dataset, batch_size, shuffle=True, num_workers=num_workers)
    val_loader = train_loader
    test_loader = DataLoader(test_dataset, batch_size, shuffle=False, num_workers=num_workers)
    
    return train_loader, val_loader, test_loader

@hydra.main(config_path=config.CONFIGS_DIR, config_name="config", version_base=None)
def main(cfg):
    print(cfg)

    pl.seed_everything(42)
    
    # 데이터 로더 준비
    train_loader, val_loader, test_loader = prepare_data(
        batch_size=cfg.data.batch_size,
        num_workers=cfg.data.num_workers
    )

    model = RegressionDNN(cfg)

    trainer = Trainer(default_root_dir=config.OUTPUTS_DIR, max_epochs=cfg.trainer.max_epochs, accelerator=cfg.trainer.accelerator)
    
    # 훈련
    trainer.fit(model, train_loader, val_loader)
    
    # 테스트
    test_results = trainer.test(model, test_loader)

    # 회귀 모델의 테스트 결과 출력
    if test_results and len(test_results) > 0:
        result = test_results[0]
        
        # 회귀 메트릭들 출력
        test_loss = result.get('test_loss', 0.0)
        test_rmse = result.get('test_rmse', 0.0)
        
        print(f"최종 테스트 손실 (MSE): {test_loss:.4f}")
        print(f"최종 테스트 RMSE: {test_rmse:.4f}")
        
        # R² Score가 있다면
        test_r2 = result.get('test_r2', None)
        if test_r2 is not None:
            print(f"최종 테스트 R² Score: {test_r2:.4f}")
    else:
        print("테스트 결과를 가져올 수 없습니다.")

if __name__ == "__main__":
    main()

/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/hydra/_internal/defaults_list.py:251: UserWarning: In 'config': Defaults list is missing `_self_`. See https://hydra.cc/docs/1.2/upgrades/1.0_to_1.1/default_composition_order for more information
  warnings.warn(msg, UserWarning)
Seed set to 42


{'data': {'batch_size': 32, 'valid_split': 0.2, 'num_workers': 4}, 'model': {'model_name': 'regression_dnn', 'input_dim': 24, 'hidden_dims': [100, 50, 25], 'output_dim': 1, 'apply_batchnorm': True, 'apply_activation': True, 'apply_dropout': True, 'dropout_ratio': 0.2}, 'optimizer': {'_target_': 'torch.optim.Adam', 'lr': 0.0001, 'weight_decay': 0.01}, 'scheduler': {'_target_': 'torch.optim.lr_scheduler.StepLR', 'step_size': 10, 'gamma': 0.5}, 'logger': {'project': 'lightning_with_hydra', 'name': 'test'}, 'callback': {'monitor': 'valid_loss', 'mode': 'min', 'patience': 3, 'logging_interval': 'epoch'}, 'trainer': {'max_epochs': 100, 'accelerator': 'auto'}}


/data/ephemeral/home/mywork/python_work/git/gx-train/src/dataset/HousePricingDataset.py:61: DtypeWarning: Columns (14,15) have mixed types. Specify dtype option on import or set low_memory=False.
  return pd.read_csv(config.HOUSE_PRICING_DATA)
💡 Tip: For seamless cloud uploads and versioning, try installing [litmodels](https://pypi.org/project/litmodels/) to enable LitModelCheckpoint, which syncs automatically with the Lightning model registry.


숫자형 변수: ['본번', '부번', '전용면적(㎡)', '계약일', '층', '건축년도', 'k-전체세대수', 'k-85㎡~135㎡이하', '건축면적', '주차대수', '좌표X', '좌표Y', '계약년', '계약월', '강남여부', '버스정류장유무', '지하철역유무']
문자형 변수: ['아파트명', '도로명', 'k-전화번호', 'k-난방방식', 'k-건설사(시공사)', '구', '동']


GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/pytorch_lightning/trainer/connectors/logger_connector/logger_connector.py:76: Starting from v1.9.0, `tensorboardX` has been removed as a dependency of the `pytorch_lightning` package, due to potential conflicts with other packages in the ML ecosystem. For this reason, `logger=True` will use `CSVLogger` as the default logger, unless the `tensorboard` or `tensorboardX` packages are found. Please `pip install lightning[extra]` or one of them to enable TensorBoard support by default
You are using a CUDA device ('NVIDIA GeForce RTX 3090') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmu

...


Detected KeyboardInterrupt, attempting graceful shutdown ...


preds:tensor([[nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan]], device='cuda:0', grad_fn=<AddmmBackward0>)
preds:tensor([[nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],
        [nan],

Error executing job with overrides: []
Traceback (most recent call last):
  File "/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/pytorch_lightning/trainer/call.py", line 48, in _call_and_handle_interrupt
    return trainer_fn(*args, **kwargs)
  File "/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/pytorch_lightning/trainer/trainer.py", line 599, in _fit_impl
    self._run(model, ckpt_path=ckpt_path)
  File "/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/pytorch_lightning/trainer/trainer.py", line 1012, in _run
    results = self._run_stage()
  File "/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/pytorch_lightning/trainer/trainer.py", line 1056, in _run_stage
    self.fit_loop.run()
  File "/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/pytorch_lightning/loops/fit_loop.py", line 216, in

SystemExit: 1

/data/ephemeral/home/mywork/python_work/git/gx-train/.venv/lib/python3.10/site-packages/IPython/core/interactiveshell.py:3587: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)
